In [1]:
#This cell allow the user to put its own parameters

import subprocess
import sqlite3
import os
import shutil

#Folder containing the folder names "Cam0, Cam1 ..."
input_folder=""

#Folder wich will contain the splats for each frames 
output_path=""

#Working folder for the coming frame folders
batchinput_folder=input_folder+"\\BatchInput"

#Folder where The gaussian splatting is stored
Gaussian_splat_folder="C:/AI/gaussian-splatting"

#Number of frames to proceed
frames=100

#First frame number
start_frame=0

#number of cameras
cams=14

#Image file name shape in the folder "Cam0, Cam1 ..."
base_path = "Cam[CAM]_[N].jpg"

In [ ]:
#This cell create a folder for each frame and store the corresponding frames in it.

lead_zero = lambda u, n: (n - len(str(u)))*"0" + str(u)

# Ask for input dir
imgs = os.path.join(os.path.dirname(__file__), input_folder)

# Save images in new folders 
os.mkdir(os.path.join(imgs, "BatchInput"))
# BatchInput/Frame[N]/input/
for i in range(frames):
    path = os.path.join(imgs, "BatchInput/Frame{}".format(i))
    os.mkdir(path)
    os.mkdir(os.path.join(path, "input"))
    for j in range(cams):
        src = os.path.join(imgs, "Cam{}".format(j+1), base_path.replace("[CAM]", str(j+1)).replace("[N]", lead_zero(start_frame + i, 8)))
        dst = os.path.join(path, "input", "{}.jpg".format(j+1))
        shutil.copyfile(src, dst)




In [2]:
#This cell declares some cleaning functions that will be helpfull in the rest of the treatment

def cleanimgtxt(imgtxtpath):
    #cette fonction prend en entrée le chemin d'accès d'un fichier images.txt généré par colmaps dont on veut retirer les ligne simpertientne de façon à entrainer un nouveau colmap avec.
    with open(imgtxtpath, 'r') as fichier:
        # Parcourir chaque ligne du fichier
        lignes=fichier.readlines()
        #print("fichier ouvert")
        #on va conserver les lignes correspondant aux indices stockés dans tokeep
        tokeep=[]
        i=0
        for ligne in lignes:
            #print(ligne)
            if "#" in ligne or "jpg" in ligne:
                tokeep.append(i)
            i+=1
        #print(tokeep)
                
    with open(imgtxtpath, 'w') as fichier:
        i=0
        #on réécrit les lignes à garder et on met une ligne vide à la place des autres
        for ligne in lignes:
            if i in tokeep:
                fichier.write(ligne)
            else :
                fichier.write("\n")
            i+=1
    print("clean image.txt finito")
    
def db_match_image_id(db_path,imagestxt_path):
    ##récupérer les id de la base de donnée
    # Ouvrir la base de données
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()

    # Sélectionner les données de la table "images"
    cursor.execute("SELECT name, image_id FROM images")
    data = cursor.fetchall()

    # Construire le dictionnaire "nom du fichier" : "id base de donnée"
    image_dict = {name: image_id for name, image_id in data}

    # Fermer la connexion à la base de données
    conn.close()

    ##faire correspondre les informations dans images.txt
    # Ouverture du fichier à images.txt à modifier
    with open(imagestxt_path, "r") as file:
        lines = file.readlines()

    with open(imagestxt_path, "w") as file:
        for line in lines:
            # Split the line into parts
            parts = line.strip().split()
            
            # Check if the line has the expectesd format
            if len(parts) == 10:
                image_id = image_dict.get(parts[-1], parts[0])
                # Replace the first number with the corrected image ID
                parts[0] = str(image_id)
                
                # Write the modified line back to the file
                new_line = " ".join(parts) + "\n"
                file.write(new_line)
            else:
                # If the line doesn't have the expected format, write it as is since this must be some other kind of information
                file.write(line)
    print("database matching finito")


In [3]:
#This cell run colmap for the first frame

def process_first_frame(i):
    project_path=batchinput_folder+"\\Frame"+str(i)+"\\distorted"
    sparse_path=batchinput_folder+"\\Frame"+str(i)+"\\distorted\\sparse\\0"
    os.mkdir(project_path)
    os.mkdir(project_path+"\\sparse")
    os.mkdir(sparse_path)
    
    
    ###copier les images
    os.mkdir(project_path+"\\images")
    
    commande = "copy "+batchinput_folder+"\\Frame"+str(i)+"\\input "+project_path+"\\images"
    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("copie du sparse de ref dans le dossier de la frame")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    
    ### constuire la database
    commande = "colmap feature_extractor \
        --database_path "+project_path+"/database.db \
        --image_path "+project_path+"/images \
        --SiftExtraction.max_image_size 1600"

    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("construction de la database")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    ###Faire trouner le matcher
    commande = "colmap exhaustive_matcher \
        --database_path "+project_path+"/database.db \
        --SiftMatching.min_num_inliers 5 \
        --SiftMatching.confidence 0.86"
    
    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("Faire tourner le matcher")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    ###Création du sparse
    commande = "colmap mapper \
        --database_path "+project_path+"/database.db \
        --image_path "+project_path+"/images \
        --output_path "+project_path+"/sparse \
        --Mapper.max_model_overlap 40 \
        --Mapper.init_min_num_inliers 80 \
        --Mapper.abs_pose_max_error 35 \
        --Mapper.abs_pose_min_num_inliers 12 \
        --Mapper.min_model_size 6"


    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("création du sparse")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)


    ##convert.py
    project_path=batchinput_folder+"\\Frame"+str(i)
    commande = "python "+Gaussian_splat_folder+"\\convert.py -s "+project_path+" --skip_matching"

    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("création du sparse")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)


process_first_frame(0)
    

copie du sparse de ref dans le dossier de la frame
Sortie standard: E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\1.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\2.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\3.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\4.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\5.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\6.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\7.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\8.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\9.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\10.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\11.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\12.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\13.jpg
E:\Cours_X\INF_img\table_basse\BatchInput\Frame0\input\14.jpg
       14 fichier(s) copi‚(s).

Sortie d'erreur: 
Code de sortie: 0
const

In [4]:
#This cell convert the colmap files "cameras.bin", "images.bin", "point3D.bin" into txt and treat them so they can be re-used for the other frames

##copie du sparse dans un folder de reserve

#création folder de reserve
os.mkdir(batchinput_folder+"\\SparseReserve")

#convert sparse en txt
commande1 = "colmap model_converter --input_path "+ batchinput_folder+"\Frame0\\distorted\\sparse\\0 --output_path "+batchinput_folder+"\\SparseReserve --output_type TXT"

# Exécution de la commande
resultat1 = subprocess.run(commande1, shell=True, capture_output=True, text=True)

# Affichage du résultat
print("Sortie standard:", resultat1.stdout)
print("Sortie d'erreur:", resultat1.stderr)
print("Code de sortie:", resultat1.returncode)

##clean du images.txt
cleanimgtxt(batchinput_folder+"\\SparseReserve\\images.txt")

##clean du points3D.txt
os.remove(batchinput_folder+"\\SparseReserve\\points3D.txt")
file=open(batchinput_folder+"\\SparseReserve\\points3D.txt","x")
file.close()

Sortie standard: 
Sortie d'erreur: 
Code de sortie: 0
finito


In [5]:
#This cell defines a function which initiate the sparse model computation for the i-th frame

def go_sparse_frame_i(i):
    project_path=batchinput_folder+"\\Frame"+str(i)+"\\distorted"
    sparse_path=batchinput_folder+"\\Frame"+str(i)+"\\distorted\\sparse\\0"
    manual_sparse_path=batchinput_folder+"\\Frame"+str(i)+"\\distorted\\manual_sparse"
    os.mkdir(project_path)
    os.mkdir(project_path+"\\sparse")
    os.mkdir(sparse_path)
    os.mkdir(manual_sparse_path)
    
    ###copier le sparse de ref dans le dossier de la frame
    commande = "copy "+batchinput_folder+"\\SparseReserve "+manual_sparse_path
    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("copie du sparse de ref dans le dossier de la frame")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    
    ###copier les images
    os.mkdir(project_path+"\\images")
    
    commande = "copy "+batchinput_folder+"\\Frame"+str(i)+"\\input "+project_path+"\\images"
    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("copie du sparse de ref dans le dossier de la frame")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    
    ### constuire la database
    commande = "colmap feature_extractor \
        --database_path "+project_path+"/database.db \
        --image_path "+project_path+"/images \
        --SiftExtraction.max_image_size 1600"

    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("construction de la database")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    db_match_image_id(project_path+"/database.db ",manual_sparse_path+"\\images.txt")
    
    ###Faire trouner le matcher
    commande = "colmap exhaustive_matcher \
        --database_path "+project_path+"/database.db \
        --SiftMatching.min_num_inliers 5 \
        --SiftMatching.confidence 0.86"

    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("Faire tourner le matcher")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    ###Création du sparse
    commande = "colmap point_triangulator \
        --database_path "+project_path+"/database.db \
        --image_path "+project_path+"/images \
        --input_path "+manual_sparse_path+" \
        --output_path "+project_path+"/sparse/0 \
        --Mapper.max_model_overlap 40 \
        --Mapper.init_min_num_inliers 80 \
        --Mapper.abs_pose_max_error 35 \
        --Mapper.abs_pose_min_num_inliers 12 \
        --Mapper.min_model_size 5"


    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("création du sparse")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)
    
    
    
    
    


In [6]:
#This Cell launch the sparse model computation for each frames

for i in range (1,frames):
    go_sparse_frame_i(i)

copie du sparse de ref dans le dossier de la frame
Sortie standard: E:\Cours_X\INF_img\Bob\BatchInput\SparseReserve\cameras.txt
E:\Cours_X\INF_img\Bob\BatchInput\SparseReserve\images.txt
E:\Cours_X\INF_img\Bob\BatchInput\SparseReserve\points3D.txt
        3 fichier(s) copi‚(s).

Sortie d'erreur: 
Code de sortie: 0
copie du sparse de ref dans le dossier de la frame
Sortie standard: E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\1.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\2.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\3.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\4.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\5.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\6.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\7.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\8.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\9.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\10.jpg
E:\Cours_X\INF_img\Bob\BatchInput\Frame1\input\11.jpg
E:\Cours_X\INF_img\Bob\BatchInp

In [4]:
#This cell defines a function which put the sparse data in the shape expected by the Gaussia splatting training for the i-th frame


def go_convert_frame_i(i):
    ###Lance convert.py de gaussian splatting en skippant le matching
    project_path=batchinput_folder+"\\Frame"+str(i)
    
    commande = "python "+Gaussian_splat_folder+"\\convert.py -s "+project_path+" --skip_matching" 


    # Exécution de la commande
    resultat = subprocess.run(commande, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("Mise en forme des fichier pour le Gaussian Splatting")
    print("Sortie standard:", resultat.stdout)
    print("Sortie d'erreur:", resultat.stderr)
    print("Code de sortie:", resultat.returncode)

In [8]:
#This Cell put the sparse data in the expected shape for each frames

for i in range(1,frames):
    go_convert_frame_i(i)

création du sparse
Sortie standard: 
Reading reconstruction

 => Reconstruction with 14 images and 4208 points

Image undistortion

Undistorting image [1/14]
Undistorting image [2/14]
Undistorting image [3/14]
Undistorting image [4/14]
Undistorting image [5/14]
Undistorting image [6/14]
Undistorting image [7/14]
Undistorting image [8/14]
Undistorting image [9/14]
Undistorting image [10/14]
Undistorting image [11/14]
Undistorting image [12/14]
Undistorting image [13/14]
Undistorting image [14/14]
Writing reconstruction...
Writing configuration...
Writing scripts...
Elapsed time: 0.012 [minutes]
Done.

Sortie d'erreur: 
Code de sortie: 0
création du sparse
Sortie standard: 
Reading reconstruction

 => Reconstruction with 14 images and 4322 points

Image undistortion

Undistorting image [1/14]
Undistorting image [2/14]
Undistorting image [3/14]
Undistorting image [4/14]
Undistorting image [5/14]
Undistorting image [6/14]
Undistorting image [7/14]
Undistorting image [8/14]
Undistorting ima

In [2]:
#This cell defines a function which plauch the Gaussian splatting training for the i-th frame

def gs_train_frame_i(i):
    ###Lance train.py du gaussian splatting sur chaque frame
    project_path=batchinput_folder+"\\Frame"+str(i)
    
    commande1 = "conda activate gaussian_splatting"

    commande2 = "python "+Gaussian_splat_folder+"//train.py -s "+project_path+" --model_path" +output_path+"\\frame"+str(i)+ "30000 --iterations 7000 "

    # Exécution de la commande
    resultat2 = subprocess.run(commande1 + " && " + commande2, shell=True, capture_output=True, text=True)

    # Affichage du résultat
    print("training de la frame : "+str(i))
    print("Sortie standard:", resultat2.stdout)
    print("Sortie d'erreur:", resultat2.stderr)
    print("Code de sortie:", resultat2.returncode)
    

In [3]:
for i in range(0,frames):
    print("début frame "+str(i))
    gs_train_frame_i(i)

début frame 0


Exception in thread Thread-6 (_readerthread):
Traceback (most recent call last):
  File "c:\Users\bapti\AppData\Local\Programs\Python\Python310\lib\threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "c:\Users\bapti\AppData\Local\Programs\Python\Python310\lib\threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "c:\Users\bapti\AppData\Local\Programs\Python\Python310\lib\subprocess.py", line 1497, in _readerthread
    buffer.append(fh.read())
  File "c:\Users\bapti\AppData\Local\Programs\Python\Python310\lib\encodings\cp1252.py", line 23, in decode
    return codecs.charmap_decode(input,self.errors,decoding_table)[0]
UnicodeDecodeError: 'charmap' codec can't decode byte 0x8f in position 6585: character maps to <undefined>


training de la frame : 0
Sortie standard: Optimizing output\frame030000
Output folder: output\frame030000 [13/12 19:30:07]
Tensorboard not available: not logging progress [13/12 19:30:07]

Reading camera 1/14
Reading camera 2/14
Reading camera 3/14
Reading camera 4/14
Reading camera 5/14
Reading camera 6/14
Reading camera 7/14
Reading camera 8/14
Reading camera 9/14
Reading camera 10/14
Reading camera 11/14
Reading camera 12/14
Reading camera 13/14
Reading camera 14/14 [13/12 19:30:07]
Loading Training Cameras [13/12 19:30:07]
[ INFO ] Encountered quite large input images (>1.6K pixels width), rescaling to 1.6K.
 If this is not desired, please explicitly specify '--resolution/-r' as 1 [13/12 19:30:07]
Loading Test Cameras [13/12 19:30:12]
Number of points at initialisation :  2032 [13/12 19:30:12]

[ITER 7000] Evaluating train: L1 0.011330869141966106 PSNR 35.2936450958252 [13/12 19:34:04]

[ITER 7000] Saving Gaussians [13/12 19:34:04]

[ITER 30000] Evaluating train: L1 0.0063028573989